### 스타벅스 매장 수와 인구수 비교

In [2]:
# 라이브러리 임포트
import pandas as pd
import json
import folium

In [3]:
# 서울시 시군구별 통계 데이터 불러오기
seoul_sgg_stat = pd.read_excel('./data/seoul_sgg_stat_202005.xlsx')
seoul_sgg_stat.head()

시군구코드  시군구명         위도          경도  스타벅스_매장수   주민등록인구    종사자수   사업체수
0  11320   도봉구  37.665861  127.031767         2  371,095   68669  18455
1  11380   은평구  37.617612  126.922700         8  474,165   87693  24179
2  11230  동대문구  37.583801  127.050700         8  374,039  143858  32994
3  11590   동작구  37.496504  126.944307        11  407,966  103915  19609
4  11545   금천구  37.460097  126.900155        10  262,337  223058  30080

In [4]:
# 서울시 시군구 행정 경계 지도 파일 불러오기
sgg_geojson_file_path = './data/seoul_sgg.geojson'
seoul_sgg_geo_2 = json.load(open(sgg_geojson_file_path, encoding='utf-8'))

In [5]:
# 주민등록 인구에 ','가 있어서 문제가 있는 상황, ',' 있으면 지도 안나옴
seoul_sgg_stat['주민등록인구']  # ','가 있어서 문제가 있는 상황

0     371,095
1     474,165
2     374,039
3     407,966
4     262,337
5     449,187
6     177,023
7     342,669
8     431,283
9     570,913
10    578,257
11    138,102
12    490,945
13    386,292
14    392,087
15    432,888
16    484,359
17    614,603
18    689,909
19    336,490
20    504,928
21    440,863
22    546,814
23    316,113
24    250,844
Name: 주민등록인구, dtype: object

In [6]:
# 문자열에서 ',' 제거 -> 타입 변환, astype('int64')
seoul_sgg_stat['주민등록인구'] = seoul_sgg_stat['주민등록인구'].str.replace(',', '').astype('int64')

In [7]:
seoul_sgg_stat['주민등록인구']

0     371095
1     474165
2     374039
3     407966
4     262337
5     449187
6     177023
7     342669
8     431283
9     570913
10    578257
11    138102
12    490945
13    386292
14    392087
15    432888
16    484359
17    614603
18    689909
19    336490
20    504928
21    440863
22    546814
23    316113
24    250844
Name: 주민등록인구, dtype: int64

In [8]:
# 서울시 시군구별 주민등록인구수 단계구분도 지도 시각화
# 진한 부분이 인구가 많음, 송파구, 강서구, 관악구순으로 인구가 많음
starbucks_choropleth = folium.Map(
    location=[37.573050, 126.979189], # 종로 구청 기준
    tiles='CartoDB dark_matter',
    zoom_start=11
)

folium.Choropleth(
    geo_data=seoul_sgg_geo_2,
    data=seoul_sgg_stat,
    columns=['시군구명', '주민등록인구'],
    fill_color = 'YlGn',
    fill_opacity=0.7,
    line_opacity=0.5,
    key_on='properties.SIG_KOR_NM'
    ).add_to(starbucks_choropleth)

starbucks_choropleth

In [9]:
seoul_sgg_stat['스타벅스_매장수'] # 데이터 확인

0      2
1      8
2      8
3     11
4     10
5     10
6     38
7      5
8      6
9     80
10    16
11    52
12    14
13    15
14    32
15    46
16    13
17    13
18    30
19    18
20    15
21    34
22    11
23    11
24    18
Name: 스타벅스_매장수, dtype: int64

In [10]:
seoul_sgg_stat['주민등록인구']  # ','가 있어서 문제가 있는 상황

0     371095
1     474165
2     374039
3     407966
4     262337
5     449187
6     177023
7     342669
8     431283
9     570913
10    578257
11    138102
12    490945
13    386292
14    392087
15    432888
16    484359
17    614603
18    689909
19    336490
20    504928
21    440863
22    546814
23    316113
24    250844
Name: 주민등록인구, dtype: int64

In [11]:
# 인구 만 명당 스타벅스 매장 수 칼럼 추가
seoul_sgg_stat['만명당_매장수'] = seoul_sgg_stat['스타벅스_매장수']/(seoul_sgg_stat['주민등록인구']/10000)

In [14]:
# 만명당 매장수 기준 상위 10% 추출 값
top = seoul_sgg_stat ['만명당_매장수'].quantile(0.9)
print(top)

# 상위 20%
top = seoul_sgg_stat ['만명당_매장수'].quantile(0.8)
print(top)

# 상위 30%
top = seoul_sgg_stat ['만명당_매장수'].quantile(0.7)
print(top)

1.2658107819231736
0.7802007915611171
0.5149153301332411


### 스타벅스 매장 수와 인구수

In [16]:
# 인구 만 명당 스타벅스 매장 수 지도 시각화
# 중구와 종로구가 인구가 가장 적은 것으로 표시되었으나 
# 스타벅스매장은 가장 많음으로 거주 인구수와 비례하지는 않음.
# 회사에 따라 커피숍이 존재
SGG_GEOJSON_FILE_PATH = './data/seoul_sgg.geojson'
seoul_sgg_geo_1 = json.load(open(SGG_GEOJSON_FILE_PATH, encoding='utf-8'))

viz_map_1 = folium.Map(
    location=[37.573050, 126.979189],
    tiles='CartoDB dark_matter',
    zoom_start=11
)

# 지도 스타일 지정 함수
def style_function(feature):
    return {
        'opacity': 0.7,
        'weight': 1,
        'fillOpacity':0,
    }

folium.GeoJson(
    seoul_sgg_geo_2,
    style_function=style_function,
).add_to(viz_map_1)
# 만명당 매장수 기준 상위 10% 추출 값, 모두 3개 매장임
top = seoul_sgg_stat ['만명당_매장수'].quantile(0.9)
for idx in seoul_sgg_stat.index:
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    r = seoul_sgg_stat.loc[idx, '만명당_매장수']
    if r > top:
        fillColor = '#FF3300' # (Red)
    else:
        fillColor = '#CCFF33' # (Green)
    
    folium.CircleMarker(
        location=[lat, lng], 
        color='#FFFF00',     # (Yellow)
        fill_color=fillColor, 
        fill_opacity=0.7,
        weight=1.5,
        radius= r * 10
    ).add_to(viz_map_1)

viz_map_1

### 5.3.4 스타벅스 매장 수와 사업체 수 비교

In [14]:
# 신규 칼럼을 생성해 값 입력
seoul_sgg_stat['종사자수_만명당_매장수'] = seoul_sgg_stat['스타벅스_매장수']/(seoul_sgg_stat['종사자수']/10000)
seoul_sgg_stat.head()

시군구코드  시군구명         위도          경도  스타벅스_매장수  주민등록인구    종사자수   사업체수  \
0  11320   도봉구  37.665861  127.031767         2  371095   68669  18455   
1  11380   은평구  37.617612  126.922700         8  474165   87693  24179   
2  11230  동대문구  37.583801  127.050700         8  374039  143858  32994   
3  11590   동작구  37.496504  126.944307        11  407966  103915  19609   
4  11545   금천구  37.460097  126.900155        10  262337  223058  30080   

    만명당_매장수  종사자수_만명당_매장수  
0  0.053895      0.291252  
1  0.168718      0.912273  
2  0.213881      0.556104  
3  0.269630      1.058557  
4  0.381189      0.448314

In [15]:
# 종사자 수 1만 명당 스타벅스 매장 수 시각화
# 서대문고, 종로구, 마포구는 붉은색원으로 상위 10%에 해당되며 
# 원의 크기로보아 사업체 종사자수와 스타벅스 매장수는 대체로 비례함.
# 강남보다 강북에 더 많다
seoul_sgg_geo_1 = json.load(open(SGG_GEOJSON_FILE_PATH, encoding='utf-8'))

viz_map_1 = folium.Map(
    location=[37.573050, 126.979189],
    tiles='CartoDB dark_matter',
    zoom_start=11
)

folium.GeoJson(
    seoul_sgg_geo_1,
    style_function=style_function,
).add_to(viz_map_1)

top = seoul_sgg_stat['종사자수_만명당_매장수'].quantile(0.9)
for idx in seoul_sgg_stat.index:
    name = seoul_sgg_stat.at[idx, '시군구명']
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    r = seoul_sgg_stat.loc[idx, '종사자수_만명당_매장수']
    
    if r > top:
        fillColor = '#FF3300'
    else:
        fillColor = '#CCFF33'
    
    folium.CircleMarker(
        location=[lat, lng], 
        color='#FFFF00', 
        fill_color=fillColor, 
        fill_opacity=0.7,
        weight=1.5,
        radius= r * 10
    ).add_to(viz_map_1)

viz_map_1